<a href="https://cognitiveclass.ai"><img src = "https://ibm.box.com/shared/static/9gegpsmnsoo25ikkbl4qzlvlyjbgxs5x.png" width = 400> </a>

<h1 align=center><font size = 5>Capstone Project Part I-- Singapore Private Property Analysis (Price, Locations, Nearby Venues, Primary Schools) </font></h1>

## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

1. <a href="#item1">Introduction</a>
    
    <a href="#subitem0">1.1 Business Problem</a>
    
    <a href="#subitem00">1.2 Target Audience</a>
 
    
2. <a href="#item2">Data</a>    
    
    <a href="#subitem1">2.1 Private Property Sale Data</a>
    
    <a href="#subitem2">2.2 Private Property Location Data</a>
    
    <a href="#subitem3">2.3 Private Property Nearby Venue Data</a>
    
    <a href="#subitem4">2.4 Private Property Nearby School Data</a>
    
    <a href="#subitem5">2.5 List of All the Dataframes to Use and Initial Visualization</a>
    
</font>
</div>

<a id='item1'></a>

## 1. Introduction

<a id='subitem0'></a>

### 1.1 Business Problem
Singapore, the city state and island country located in Southeast Asia, is one of the original Four Asian Tigers. Having surpassed its peers in terms of GDP per capita, Singapore has one of the highest stand of living in Asia-Pacific [1]. With its "forward-thinking policies", Singapore has delivered on world-class infrastructures, and has become renowned for its airports, housing, safety, as well as the advanced infocomm networks, making Singapore one of the most attractive cities to live in Asia [2]. 

Singapore's private properties, therefore, continue to be highly sought-after by not only Singaporeans but also foreign investors. Buying properties is never a trivial decision to make, which becomes particularly true if the context is in Singapore with the high prices of its private properties. However, there are way too many factors that need to be considered in the decision making process of buying properties. Data analyses therefore can be very useful in this aspect thanks to its capability to help in decision-making processes. 

<a id='subitem00'></a>

### 1.2 Target Audience
This project aims to collect data about the private properties in Singapore, and to perform data analyses on the collected data. Potential buyers of Singapore's private properties as well as property agents can benefit from this project in terms of better understanding of the available properties in market, cross-comparison of the properties, as well as information about near-by venues that the future property owners could enjoy. One special bonus section will be dedicated to home buyers with preschool kids, with the primary schools that are nearby properties be sorted out and analyzed for them. Potential home buyers or investors can therefore make more informed decisions based on the results of this project, and property agents could also provide better recommendations based on the report to their customers.

[1]. https://en.wikipedia.org/wiki/Singapore

[2]. https://www.reuters.com/brandfeatures/infrastructure2030/singapore-hub


<a id='item2'></a>

## 2. Data

Based on the definition of the business problem, essential data for the analysis include:

* Private properties for sale in the market
* Recorded sale prices of the properties
* Locations of the properties
* Total units for each properties
* Venues nearby the properties
* Primary schools that are located within 1km of the properties

Due to the data size and availability constraints, the analyses will focus on the properties directly sold by all developers in a six-month time frame (from 2019 October to 2020 March). 

Following data sources will be utilized to generate the required data:
* The private property sale records from Singapore URA website [3]. 
* The location data of each property extracted from **geopy.geocoders**
* A number of venues with their categories within a specified distance (1km) of every single property obtained via **Foursquare API**
* All the primary schools within a distance of 1km of every single property obtained via **Foursquare API**

[3]. https://www.ura.gov.sg/realEstateIIWeb/price/search.action

#### Import essential libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

import io
import requests

print('Libraries imported.')

Libraries imported.


#### Define Foursquare credentials

In [2]:
CLIENT_ID = 'OV32LUAEQG2RHIS4WBUEIRTR0BPOQQDYANRHECEKBJMBKDL4' # your Foursquare ID
CLIENT_SECRET = 'LPOAE4QCO02XWITIXU1DTWENZOECEKYMOU0EPNFIOO3IJTKJ' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: OV32LUAEQG2RHIS4WBUEIRTR0BPOQQDYANRHECEKBJMBKDL4
CLIENT_SECRET:LPOAE4QCO02XWITIXU1DTWENZOECEKYMOU0EPNFIOO3IJTKJ


<a id='subitem1'></a> 

### 2.1 Private property sale data

#### Retrieve property data from the CSV files downloaded from URA website, assign to the dataframes:

In [3]:
def readdata(dffile):
    cp_df=pd.read_csv(dffile, header=1)
    cp_df.head()
    median_col=[col for col in cp_df.columns if 'Median' in col]
    #median_col[0]
    gcp_df=cp_df[cp_df[median_col[0]]!=' - ']
    gcp_df.reset_index(drop=True, inplace=True)
    gcp_df.dropna(how='any', inplace=True)
    return gcp_df

cp_df1=readdata("price201910.csv")
cp_df2=readdata("price201911.csv")
cp_df3=readdata("price201912.csv")
cp_df4=readdata("price202001.csv")
cp_df5=readdata("price202002.csv")
cp_df6=readdata("price202003.csv")

cp_df1['Month']= "2019-10"
cp_df2['Month']= "2019-11"
cp_df3['Month']= "2019-12"
cp_df4['Month']= "2020-1"
cp_df5['Month']= "2020-2"
cp_df6['Month']= "2020-3"

frames = [cp_df1, cp_df2, cp_df3, cp_df4, cp_df5, cp_df6]

result = pd.concat(frames)
result.drop(columns=["S/N"], inplace=True)
#print(result.info())
newresult=result
newresult.columns=['Property', 'Street', 'Developer', 'Type', 'Locality', 'Total Units', 'Launched', 'Sold', 'Unsold',\
                  'Unsold1', 'Launched1', 'Sold1', 'Median Price', 'Low', 'High', 'Month']
newresult['Median Price'] = newresult['Median Price'].astype(float)
#newresult.info()
#Dataframe with all month information
cft_df=newresult[['Property', 'Street', 'Developer', 'Type', 'Locality', 'Total Units', 'Median Price', 'Month']]
cft_df.head()
#Dataframe with average month information
cfa_df=cft_df.drop(columns=['Month'])
cfa_df=cfa_df.groupby('Property').agg(
    {'Total Units': 'mean', 'Median Price': 'mean','Property': lambda x: x.iloc[0],\
     'Street': lambda x: x.iloc[0], 'Developer': lambda x: x.iloc[0],\
     'Type': lambda x: x.iloc[0], 'Locality': lambda x: x.iloc[0]})


print("Number of private resident projects is {}".format(len(cfa_df['Property'].unique())))
print("Shape of the combined dataframe is {}".format(cfa_df.shape))
cfa_df.head()

Number of private resident projects is 111
Shape of the combined dataframe is (111, 7)


/Users/JUMP/anaconda/lib/python3.6/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


Total Units  Median Price    Property           Street  \
Property                                                             
10 EVELYN          56.0        2807.0   10 EVELYN      EVELYN ROAD   
120 GRANGE         56.0        3234.0  120 GRANGE      GRANGE ROAD   
19 NASSIM         101.0        3351.0   19 NASSIM      NASSIM HILL   
1953               58.0        1855.0        1953  TESSENSOHN ROAD   
3 CUSCADEN         96.0        3551.6  3 CUSCADEN    CUSCADEN WALK   

                                 Developer        Type Locality  
Property                                                         
10 EVELYN     Creative Investments Pte Ltd  Non-Landed      CCR  
120 GRANGE              RH Orchard Pte Ltd  Non-Landed      CCR  
19 NASSIM   Parksville Development Pte Ltd  Non-Landed      CCR  
1953                Oxley Amethyst Pte Ltd  Non-Landed      RCR  
3 CUSCADEN          SL Capital (2) Pte Ltd  Non-Landed      CCR

<a id='subitem2'></a> 

### 2.2 Private property location data

#### To retrieve location data with latitude and longitude for every property from geocoder

In [4]:
#Try out the geocoder with a single example
import geocoder
entry=cfa_df.iloc[0, :]
locat=None
while locat==None:
    g = geocoder.arcgis('{}, {}, {}'.format(entry['Property'], entry['Street'], 'Singapore'))
    locat=g.latlng
locat

[1.316736000000006, 103.83961950000003]

In [5]:
cfa_df['Latitude']=None
cfa_df['Longitude']=None
for i in range(cfa_df.shape[0]):
    entry=cfa_df.iloc[i, :]
    locat=None
    while locat==None:
        g = geocoder.arcgis('{}, {}, {}'.format(entry['Property'], entry['Street'], 'Singapore'))
        locat=g.latlng
    entry['Latitude']=locat[0]
    entry['Longitude']=locat[1]
    cfa_df.iloc[i, :]=entry
print(cfa_df.shape)
cfa_df.head()

/Users/JUMP/anaconda/lib/python3.6/site-packages/ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
/Users/JUMP/anaconda/lib/python3.6/site-packages/ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.


(111, 9)


Total Units  Median Price    Property           Street  \
Property                                                             
10 EVELYN          56.0        2807.0   10 EVELYN      EVELYN ROAD   
120 GRANGE         56.0        3234.0  120 GRANGE      GRANGE ROAD   
19 NASSIM         101.0        3351.0   19 NASSIM      NASSIM HILL   
1953               58.0        1855.0        1953  TESSENSOHN ROAD   
3 CUSCADEN         96.0        3551.6  3 CUSCADEN    CUSCADEN WALK   

                                 Developer        Type Locality Latitude  \
Property                                                                   
10 EVELYN     Creative Investments Pte Ltd  Non-Landed      CCR  1.31674   
120 GRANGE              RH Orchard Pte Ltd  Non-Landed      CCR  1.29967   
19 NASSIM   Parksville Development Pte Ltd  Non-Landed      CCR  1.30665   
1953                Oxley Amethyst Pte Ltd  Non-Landed      RCR  1.31523   
3 CUSCADEN          SL Capital (2) Pte Ltd  Non-Landed      CCR  1.30387   

           Longitude  
Property              
10 EVELYN     103.84  
120 GRANGE   103.825  
19 NASSIM    103.821  
1953         103.856  
3 CUSCADEN   103.829

In [6]:
cfa_df.reset_index(drop=True, inplace=True)
cfa_df.head()

Total Units  Median Price    Property           Street  \
0         56.0        2807.0   10 EVELYN      EVELYN ROAD   
1         56.0        3234.0  120 GRANGE      GRANGE ROAD   
2        101.0        3351.0   19 NASSIM      NASSIM HILL   
3         58.0        1855.0        1953  TESSENSOHN ROAD   
4         96.0        3551.6  3 CUSCADEN    CUSCADEN WALK   

                        Developer        Type Locality Latitude Longitude  
0    Creative Investments Pte Ltd  Non-Landed      CCR  1.31674    103.84  
1              RH Orchard Pte Ltd  Non-Landed      CCR  1.29967   103.825  
2  Parksville Development Pte Ltd  Non-Landed      CCR  1.30665   103.821  
3          Oxley Amethyst Pte Ltd  Non-Landed      RCR  1.31523   103.856  
4          SL Capital (2) Pte Ltd  Non-Landed      CCR  1.30387   103.829

<a id='subitem3'></a> 

### 2.3 Private property nearby venue data

#### To retrieve nearby venues within 1km and a limit of 100 venues for every property via Foursquare

In [9]:
def getNearbyVenues(names, latitudes, longitudes, radius=1000):
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        #print(results)
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Property', 
                  'Property Latitude', 
                  'Property Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

LIMIT = 100
property_venues = getNearbyVenues(names=cfa_df['Property'],
                                   latitudes=cfa_df['Latitude'],
                                   longitudes=cfa_df['Longitude']
                                  )
property_venues.head()

10 EVELYN
[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53492538498e0f29cc1f4da9', 'name': 'Ah Chew Desserts 阿秋甜品 (Ah Chew Desserts)', 'location': {'address': '181 Thomson Rd Goldhill Centre', 'lat': 1.318411, 'lng': 103.843714, 'labeledLatLngs': [{'label': 'display', 'lat': 1.318411, 'lng': 103.843714}], 'distance': 492, 'postalCode': '307627', 'cc': 'SG', 'city': 'Singapore', 'country': 'Singapore', 'formattedAddress': ['181 Thomson Rd Goldhill Centre', '307627', 'Singapore']}, 'categories': [{'id': '4bf58dd8d48988d1d0941735', 'name': 'Dessert Shop', 'pluralName': 'Dessert Shops', 'shortName': 'Desserts', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/dessert_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-53492538498e0f29cc1f4da9-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type':

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b9c5ec3f964a520766336e3', 'name': 'Basilico', 'location': {'address': 'Regent Hotel', 'crossStreet': '1 Cuscaden Rd.', 'lat': 1.304627, 'lng': 103.824892, 'labeledLatLngs': [{'label': 'display', 'lat': 1.304627, 'lng': 103.824892}], 'distance': 554, 'postalCode': '249715', 'cc': 'SG', 'city': 'Singapore', 'country': 'Singapore', 'formattedAddress': ['Regent Hotel (1 Cuscaden Rd.)', '249715', 'Singapore']}, 'categories': [{'id': '4bf58dd8d48988d110941735', 'name': 'Italian Restaurant', 'pluralName': 'Italian Restaurants', 'shortName': 'Italian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/italian_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4b9c5ec3f964a520766336e3-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reas

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4e2fb4ded1646b407b90c8f7', 'name': 'Tanglin Gate | Singapore Botanic Gardens', 'location': {'address': 'Cluny Rd.', 'crossStreet': 'Napier Rd.', 'lat': 1.3071308997488138, 'lng': 103.81861209869385, 'labeledLatLngs': [{'label': 'display', 'lat': 1.3071308997488138, 'lng': 103.81861209869385}], 'distance': 325, 'cc': 'SG', 'city': 'Singapore', 'country': 'Singapore', 'formattedAddress': ['Cluny Rd. (Napier Rd.)', 'Singapore']}, 'categories': [{'id': '4bf58dd8d48988d163941735', 'name': 'Park', 'pluralName': 'Parks', 'shortName': 'Park', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/park_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4e2fb4ded1646b407b90c8f7-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonNa

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '51a2af4d498ec025802f527d', 'name': 'MTR 1924', 'location': {'address': '438 Serangoon Road', 'crossStreet': 'opp Perumal Temple', 'lat': 1.312972832430169, 'lng': 103.85637116555631, 'labeledLatLngs': [{'label': 'display', 'lat': 1.312972832430169, 'lng': 103.85637116555631}], 'distance': 253, 'postalCode': '218133', 'cc': 'SG', 'city': 'Singapore', 'country': 'Singapore', 'formattedAddress': ['438 Serangoon Road (opp Perumal Temple)', '218133', 'Singapore']}, 'categories': [{'id': '4bf58dd8d48988d10f941735', 'name': 'Indian Restaurant', 'pluralName': 'Indian Restaurants', 'shortName': 'Indian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/indian_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-51a2af4d498ec025802f527d-0'}, {'reasons': {'count': 0, 'items': [{'summary'

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b05880bf964a520d0ad22e3', 'name': 'Four Seasons Hotel Singapore', 'location': {'address': '190 Orchard Blvd.', 'crossStreet': 'Paterson Rd.', 'lat': 1.3051133132689718, 'lng': 103.82867574691772, 'labeledLatLngs': [{'label': 'display', 'lat': 1.3051133132689718, 'lng': 103.82867574691772}], 'distance': 161, 'postalCode': '248646', 'cc': 'SG', 'city': 'Singapore', 'state': 'Central Singapore', 'country': 'Singapore', 'formattedAddress': ['190 Orchard Blvd. (Paterson Rd.)', '248646', 'Singapore']}, 'categories': [{'id': '4bf58dd8d48988d1fa931735', 'name': 'Hotel', 'pluralName': 'Hotels', 'shortName': 'Hotel', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/hotel_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4b05880bf964a520d0ad22e3-0'}, {'reasons': {'count': 0, 'items

...

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '5c174105c0c0840025cdf11c', 'name': 'Flagwhite', 'location': {'address': '106 Jalan Jurong Kechil', 'lat': 1.340791, 'lng': 103.772371, 'labeledLatLngs': [{'label': 'display', 'lat': 1.340791, 'lng': 103.772371}], 'distance': 448, 'postalCode': '598604', 'cc': 'SG', 'city': 'Bukit Timah', 'state': 'Singapore', 'country': 'Singapore', 'formattedAddress': ['106 Jalan Jurong Kechil', '598604', 'Singapore']}, 'categories': [{'id': '4bf58dd8d48988d16d941735', 'name': 'Café', 'pluralName': 'Cafés', 'shortName': 'Café', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/cafe_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-5c174105c0c0840025cdf11c-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b7fa2e2f964a520a73730e3', 'name': 'Sembawang Park', 'location': {'address': 'Sembawang Road End', 'lat': 1.461280688963049, 'lng': 103.83650779724121, 'labeledLatLngs': [{'label': 'display', 'lat': 1.461280688963049, 'lng': 103.83650779724121}], 'distance': 209, 'cc': 'SG', 'city': 'Singapore', 'country': 'Singapore', 'formattedAddress': ['Sembawang Road End', 'Singapore']}, 'categories': [{'id': '4bf58dd8d48988d163941735', 'name': 'Park', 'pluralName': 'Parks', 'shortName': 'Park', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/park_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4b7fa2e2f964a520a73730e3-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '556853ec498e362ccb7b7cf8', 'name': 'Nobiro Japanese Restaurant & Sake bar', 'location': {'address': '108 Faber Drive', 'lat': 1.3204109638997454, 'lng': 103.75656104094843, 'labeledLatLngs': [{'label': 'display', 'lat': 1.3204109638997454, 'lng': 103.75656104094843}], 'distance': 355, 'postalCode': '129418', 'cc': 'SG', 'country': 'Singapore', 'formattedAddress': ['108 Faber Drive', '129418', 'Singapore']}, 'categories': [{'id': '4bf58dd8d48988d111941735', 'name': 'Japanese Restaurant', 'pluralName': 'Japanese Restaurants', 'shortName': 'Japanese', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/japanese_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-556853ec498e362ccb7b7cf8-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', '

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4b174179f964a52049c423e3', 'name': "Huber's Butchery & Bistro", 'location': {'address': '18A Dempsey Hill', 'lat': 1.306698259895692, 'lng': 103.81015686472739, 'labeledLatLngs': [{'label': 'display', 'lat': 1.306698259895692, 'lng': 103.81015686472739}], 'distance': 921, 'postalCode': '249677', 'cc': 'SG', 'city': 'Singapore', 'country': 'Singapore', 'formattedAddress': ['18A Dempsey Hill', '249677', 'Singapore']}, 'categories': [{'id': '4bf58dd8d48988d11d951735', 'name': 'Butcher', 'pluralName': 'Butchers', 'shortName': 'Butcher', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_butcher_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4b174179f964a52049c423e3-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName'

Property  Property Latitude  Property Longitude  \
0  10 EVELYN           1.316736           103.83962   
1  10 EVELYN           1.316736           103.83962   
2  10 EVELYN           1.316736           103.83962   
3  10 EVELYN           1.316736           103.83962   
4  10 EVELYN           1.316736           103.83962   

                                      Venue  Venue Latitude  Venue Longitude  \
0  Ah Chew Desserts 阿秋甜品 (Ah Chew Desserts)        1.318411       103.843714   
1                       Hai Yan BBQ Seafood        1.312084       103.839500   
2                                    Udders        1.318253       103.843948   
3             Chui Huay Lim Teochew Cuisine        1.313970       103.841545   
4                         Starbucks Reserve        1.317673       103.844021   

       Venue Category  
0        Dessert Shop  
1  Seafood Restaurant  
2      Ice Cream Shop  
3  Chinese Restaurant  
4         Coffee Shop

<a id='subitem4'></a> 

### 2.4 Private property nearby school data

In [10]:
school_count=property_venues['Venue'].str.contains('School').sum()
if school_count>0:
    print ("There are {} schools".format(school_count))
property_venues.head()

school_index=property_venues['Venue'].str.contains('School')
property_venues[school_index]
property_venues.shape

There are 6 schools


(7321, 7)

In [11]:
property_venues.head()

Property  Property Latitude  Property Longitude  \
0  10 EVELYN           1.316736           103.83962   
1  10 EVELYN           1.316736           103.83962   
2  10 EVELYN           1.316736           103.83962   
3  10 EVELYN           1.316736           103.83962   
4  10 EVELYN           1.316736           103.83962   

                                      Venue  Venue Latitude  Venue Longitude  \
0  Ah Chew Desserts 阿秋甜品 (Ah Chew Desserts)        1.318411       103.843714   
1                       Hai Yan BBQ Seafood        1.312084       103.839500   
2                                    Udders        1.318253       103.843948   
3             Chui Huay Lim Teochew Cuisine        1.313970       103.841545   
4                         Starbucks Reserve        1.317673       103.844021   

       Venue Category  
0        Dessert Shop  
1  Seafood Restaurant  
2      Ice Cream Shop  
3  Chinese Restaurant  
4         Coffee Shop

In [12]:
school_count=property_venues['Venue Category'].str.contains('School').sum()
if school_count>0:
    print ("There are {} schools".format(school_count))
property_venues.head()

school_index=property_venues['Venue Category'].str.contains('School')
property_venues[school_index]

There are 2 schools


Property  Property Latitude  Property Longitude  \
508   77 @ EAST COAST           1.317867          103.949770   
1323     CASA AL MARE           1.378203          103.959602   

                                 Venue  Venue Latitude  Venue Longitude  \
508   Indoor Sports Hall @ Bedok South        1.326071       103.951059   
1323          Hai Sing Catholic School        1.375020       103.955616   

     Venue Category  
508          School  
1323    High School

#### Since no primary schools are retrieved in this manner, a different approach is applied to retrieve all the primary schools within 1km for every property via Foursquare

In [13]:
categories="4f4533804b9074f6e4fb0105"#category ID for elementary school
#GET https://api.foursquare.com/v2/venues/categories
def getNearbySchools(names, latitudes, longitudes, radius=1000):
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT,
            categories)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Property', 
                  'Property Latitude', 
                  'Property Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

LIMIT = 100
property_school = getNearbySchools(names=cfa_df['Property'],
                                   latitudes=cfa_df['Latitude'],
                                   longitudes=cfa_df['Longitude']
                                  )
property_school.head()

10 EVELYN
120 GRANGE
19 NASSIM
1953
3 CUSCADEN
35 GILSTEAD
77 @ EAST COAST
AFFINITY AT SERANGOON
AMBER 45
AMBER PARK
ARENA RESIDENCES
ARTRA
AVENUE SOUTH RESIDENCE
BELGRAVIA GREEN
BIJOU
BOULEVARD 88
BUKIT 828
CARPMAEL THIRTY-EIGHT
CASA AL MARE
CAYMAN RESIDENCES
COASTLINE RESIDENCES
CUSCADEN RESERVE
DAINTREE RESIDENCE
DAIRY FARM RESIDENCES
DALVEY HAUS
DUNEARN 386
FOREST WOODS
FOURTH AVENUE RESIDENCES
FYVE DERBYSHIRE
GEM RESIDENCES
GRANDEUR PARK RESIDENCES
HAUS ON HANDY
INFINI AT EAST COAST
JADESCAPE
JUI RESIDENCES
JUNIPER HILL
KANDIS RESIDENCE
KENT RIDGE HILL RESIDENCES
KOPAR AT NEWTON
LA MARIPOSA
LATTICE ONE
LE QUEST
LEEDON GREEN
MARGARET VILLE
MARTIN MODERN
MAYFAIR GARDENS
MAYFAIR MODERN
MEYER MANSION
MIDTOWN BAY
MIDWOOD
MONT BOTANIK RESIDENCE
NEEM TREE
NEU AT NOVENA
NIM COLLECTION
NORTHWAVE
OLA
OLLOI
ONE DRAYCOTT
ONE HOLLAND VILLAGE RESIDENCES
ONE MEYER
ONE PEARL BANK
ONE TREE HILL COLLECTION
PARC BOTANNIA
PARC CANBERRA
PARC CLEMATIS
PARC ESTA
PARC KOMO
PARK COLONIAL
PARK PLACE RESIDE

Property  Property Latitude  Property Longitude  \
0   10 EVELYN           1.316736           103.83962   
1   10 EVELYN           1.316736           103.83962   
2   10 EVELYN           1.316736           103.83962   
3  120 GRANGE           1.299670           103.82541   
4  120 GRANGE           1.299670           103.82541   

                             Venue  Venue Latitude  Venue Longitude  \
0                        elan soma        1.317493       103.844239   
1  St. Joseph's Institution Junior        1.317042       103.845477   
2          Learn Different Academy        1.310016       103.841827   
3                     Kindernomics        1.306514       103.828716   
4         Alexandra Primary School        1.291213       103.823912   

      Venue Category  
0  Elementary School  
1  Elementary School  
2  Elementary School  
3  Elementary School  
4  Elementary School

#### As some other schools are also retreived though the category was set to be elementary school, the dataframe is extracted to sort out only primary schools. 

In [14]:
ps_df=property_school[property_school['Venue'].str.contains('Primary School')]
ps_df.reset_index(drop=True, inplace=True)
ps_df

Property  Property Latitude  Property Longitude  \
0                  120 GRANGE           1.299670          103.825410   
1                       ARTRA           1.290528          103.816572   
2                       ARTRA           1.290528          103.816572   
3      AVENUE SOUTH RESIDENCE           1.276497          103.830543   
4      AVENUE SOUTH RESIDENCE           1.276497          103.830543   
5      AVENUE SOUTH RESIDENCE           1.276497          103.830543   
6                   BUKIT 828           1.373740          103.762920   
7                   BUKIT 828           1.373740          103.762920   
8                CASA AL MARE           1.378203          103.959602   
9                CASA AL MARE           1.378203          103.959602   
10         DAINTREE RESIDENCE           1.339704          103.765960   
11      DAIRY FARM RESIDENCES           1.366110          103.770194   
12                DUNEARN 386           1.324539          103.811805   
13                DUNEARN 386           1.324539          103.811805   
14               FOREST WOODS           1.350925          103.876437   
15             GEM RESIDENCES           1.336918          103.852408   
16              HAUS ON HANDY           1.299586          103.846491   
17             JUI RESIDENCES           1.326020          103.866620   
18                LATTICE ONE           1.373460          103.827185   
19                   LE QUEST           1.356600          103.741100   
20                   LE QUEST           1.356600          103.741100   
21               LEEDON GREEN           1.315872          103.802229   
22             MARGARET VILLE           1.299330          103.803010   
23            MAYFAIR GARDENS           1.338435          103.781844   
24                  NORTHWAVE           1.441925          103.808227   
25                  NORTHWAVE           1.441925          103.808227   
26                  NORTHWAVE           1.441925          103.808227   
27                        OLA           1.398847          103.891336   
28                        OLA           1.398847          103.891336   
29             ONE PEARL BANK           1.283100          103.840250   
30              PARC BOTANNIA           1.398437          103.879102   
31              PARC BOTANNIA           1.398437          103.879102   
32              PARC CLEMATIS           1.318972          103.760291   
33              PARC CLEMATIS           1.318972          103.760291   
34              PARC CLEMATIS           1.318972          103.760291   
35                  PARC ESTA           1.318980          103.903930   
36                  PARC ESTA           1.318980          103.903930   
37                 PARKSUITES           1.316403          103.782915   
38        PARKWOOD COLLECTION           1.367391          103.890186   
39        PARKWOOD COLLECTION           1.367391          103.890186   
40             PIERMONT GRAND           1.405137          103.894986   
41       RIVERCOVE RESIDENCES           1.392314          103.884543   
42       RIVERCOVE RESIDENCES           1.392314          103.884543   
43       RIVERCOVE RESIDENCES           1.392314          103.884543   
44                RV ALTITUDE           1.293137          103.827832   
45                RV ALTITUDE           1.293137          103.827832   
46  SENGKANG GRAND RESIDENCES           1.383953          103.890296   
47  SENGKANG GRAND RESIDENCES           1.383953          103.890296   
48  SENGKANG GRAND RESIDENCES           1.383953          103.890296   
49                SKY EVERTON           1.275715          103.838646   
50                      TEDGE           1.320830          103.917990   
51               THE ADDITION           1.331050          103.867300   
52      THE ENCLAVE . HOLLAND           1.323301          103.784996   
53    THE FLORENCE RESIDENCES           1.369008          103.881177   
54    THE FLORENCE RESIDENCES           1.369008          103

<a id='subitem5'></a> 

### 2.5 List of all the dataframes and initial visualization

#### List of all the dataframes

##### Dataframe with property information

In [15]:
cfa_df.head()

Total Units  Median Price    Property           Street  \
0         56.0        2807.0   10 EVELYN      EVELYN ROAD   
1         56.0        3234.0  120 GRANGE      GRANGE ROAD   
2        101.0        3351.0   19 NASSIM      NASSIM HILL   
3         58.0        1855.0        1953  TESSENSOHN ROAD   
4         96.0        3551.6  3 CUSCADEN    CUSCADEN WALK   

                        Developer        Type Locality Latitude Longitude  
0    Creative Investments Pte Ltd  Non-Landed      CCR  1.31674    103.84  
1              RH Orchard Pte Ltd  Non-Landed      CCR  1.29967   103.825  
2  Parksville Development Pte Ltd  Non-Landed      CCR  1.30665   103.821  
3          Oxley Amethyst Pte Ltd  Non-Landed      RCR  1.31523   103.856  
4          SL Capital (2) Pte Ltd  Non-Landed      CCR  1.30387   103.829

In [16]:
print(cfa_df.shape)

(111, 9)


##### Dataframe with property nearby venue information

In [17]:
property_venues.head()

Property  Property Latitude  Property Longitude  \
0  10 EVELYN           1.316736           103.83962   
1  10 EVELYN           1.316736           103.83962   
2  10 EVELYN           1.316736           103.83962   
3  10 EVELYN           1.316736           103.83962   
4  10 EVELYN           1.316736           103.83962   

                                      Venue  Venue Latitude  Venue Longitude  \
0  Ah Chew Desserts 阿秋甜品 (Ah Chew Desserts)        1.318411       103.843714   
1                       Hai Yan BBQ Seafood        1.312084       103.839500   
2                                    Udders        1.318253       103.843948   
3             Chui Huay Lim Teochew Cuisine        1.313970       103.841545   
4                         Starbucks Reserve        1.317673       103.844021   

       Venue Category  
0        Dessert Shop  
1  Seafood Restaurant  
2      Ice Cream Shop  
3  Chinese Restaurant  
4         Coffee Shop

In [18]:
print(property_venues.shape)

(7321, 7)


##### Dataframe with property nearby school information

In [19]:
ps_df.head()

Property  Property Latitude  Property Longitude  \
0              120 GRANGE           1.299670          103.825410   
1                   ARTRA           1.290528          103.816572   
2                   ARTRA           1.290528          103.816572   
3  AVENUE SOUTH RESIDENCE           1.276497          103.830543   
4  AVENUE SOUTH RESIDENCE           1.276497          103.830543   

                         Venue  Venue Latitude  Venue Longitude  \
0     Alexandra Primary School        1.291213       103.823912   
1  Gan Eng Seng Primary School        1.285765       103.815187   
2     Alexandra Primary School        1.291213       103.823912   
3     Radin Mas Primary School        1.274728       103.823972   
4       Zhangde Primary School        1.284212       103.826825   

      Venue Category  
0  Elementary School  
1  Elementary School  
2  Elementary School  
3  Elementary School  
4  Elementary School

In [20]:
print(ps_df.shape)

(64, 7)


##### Additional Information: Dataframe with all the Singpaore primary school information allps_df

In [21]:
##### Download primary school data from the link, assign to the dataframe allps_df:
url="https://en.wikipedia.org/wiki/List_of_primary_schools_in_Singapore"
c=pd.read_html(url)
allps_df = c[0]
print('Data downloaded!')
print(allps_df.shape)
allps_df.head()

Data downloaded!
(190, 7)


Name                Funding   Type      Area[3]  \
0      Admiralty Primary School             Government  Mixed    Woodlands   
1  Ahmad Ibrahim Primary School             Government  Mixed       Yishun   
2                Ai Tong School  Government-aided, SAP  Mixed       Bishan   
3      Alexandra Primary School             Government  Mixed  Bukit Merah   
4   Anchor Green Primary School             Government  Mixed     Sengkang   

                                          Notes Website  School Code  
0                                           NaN     [1]       1744.0  
1                                           NaN     [2]       1738.0  
2  Affiliated to Singapore Hokkien Huay Kuan[4]     [3]       5625.0  
3                                           NaN     [4]       1266.0  
4                                           NaN     [5]       1254.0

#### Initial visualization 

#### To obtain the latitude and longitude of Singapore

In [22]:
address = 'Singapore'
geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Singapore are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Singapore are 1.357107, 103.8194992.


#### Create map of Singapore using latitude and longitude values with the property popup

In [23]:
# create map of Singapore using latitude and longitude values
map_singapore = folium.Map(location=[latitude, longitude], zoom_start=11.5)
# add markers to map
for lat, lng, prop, deve in zip(cfa_df['Latitude'], cfa_df['Longitude'], cfa_df['Property'], cfa_df['Developer']):
    label = '{} by {}'.format(prop, deve)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_singapore)  
    
map_singapore

<a id='item3'></a>